In [1]:
a=[]
a = [0] * 12 + [1] * 12
print(a)

[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]


In [2]:
a = [item for i in range(6) for item in [i]*2]*2
print(a)

[0, 0, 1, 1, 2, 2, 3, 3, 4, 4, 5, 5, 0, 0, 1, 1, 2, 2, 3, 3, 4, 4, 5, 5]


In [2]:
import random
import pandas as pd

names = ["Amplitude", "el_1", "el_2", "el_3", "el_4"]
random_lists = [[round(random.uniform(1.0, 100.0),2) for _ in range(24)] for _ in range(len(names))]
result = dict(zip(names, random_lists))
print(result)

{'Amplitude': [1.99, 91.79, 13.0, 49.52, 1.8, 2.71, 11.61, 53.49, 41.7, 61.72, 40.5, 78.64, 14.65, 7.18, 48.62, 25.15, 56.31, 65.45, 60.96, 62.49, 13.39, 60.83, 21.83, 5.48], 'el_1': [10.87, 92.67, 1.51, 71.3, 31.89, 12.55, 19.45, 64.85, 60.14, 59.47, 24.82, 1.19, 89.8, 93.8, 80.45, 45.46, 2.54, 47.2, 96.37, 66.84, 99.42, 91.32, 36.32, 39.13], 'el_2': [11.43, 3.61, 70.82, 64.46, 40.87, 50.52, 21.66, 94.23, 12.26, 93.26, 97.33, 15.75, 69.45, 54.57, 77.57, 8.81, 61.68, 57.35, 88.2, 88.12, 22.75, 58.8, 42.18, 44.98], 'el_3': [22.97, 46.33, 50.34, 75.46, 1.55, 95.48, 98.39, 73.13, 27.93, 44.62, 97.46, 49.26, 14.5, 50.12, 78.56, 45.72, 17.19, 9.3, 28.53, 47.34, 63.58, 98.48, 91.76, 30.23], 'el_4': [23.03, 40.06, 67.79, 67.0, 78.83, 46.87, 73.51, 92.93, 7.97, 53.44, 51.63, 13.99, 54.62, 10.86, 95.42, 21.5, 15.82, 38.4, 65.84, 12.86, 32.59, 67.97, 34.97, 18.34]}


In [120]:
impulses = pd.read_csv('d:/Work/2024/data2024/raw/raw_Na2SO4__28.02.24-12.43.19.dat', delimiter=',', header=None)
impulses.columns = ['Impulse', 'Step', 'Channel'] + [str(i) for i in range(1, 601)]
impulses[['Impulse', 'Step', 'Channel']] = impulses[['Impulse', 'Step', 'Channel']].astype('category')
impulses['Threshold'] = impulses.iloc[:,len(impulses.columns)-100:len(impulses.columns)].mean(axis=1)
impulses.loc[:,[str(i) for i in range(1, 601)]]
impulses['Sum'] = impulses.iloc[:,7:70].sum(axis=1)
unique_steps = impulses['Step'].unique()
#print(impulses.loc[impulses['Channel'] == 'Analyt'].iloc[:50][['Impulse','Channel', 'Threshold', 'Sum']])
print(impulses.iloc[24:27])

   Impulse  Step Channel         1         2         3         4         5  \
24      12  1020   Reper  0.000836  0.001803  0.000514  0.000836  0.000514   
25      12  1020  Analyt -0.080388 -0.078777 -0.072008 -0.064595 -0.065884   
26      13  1020   Reper  0.001481  0.000836  0.000514  0.000836  0.001158   

           6         7  ...       593       594       595       596       597  \
24  0.000836  0.000836  ...  0.000836  0.000514  0.000514  0.001158  0.000836   
25 -0.066206 -0.071363  ... -0.076843 -0.080066 -0.077165 -0.085545 -0.080066   
26  0.000514  0.000514  ...  0.000514  0.000836  0.000191  0.000836  0.000836   

         598       599       600  Threshold       Sum  
24  0.003092  0.000514  0.000836   0.000778  7.354803  
25 -0.075876 -0.090702 -0.102628  -0.077620  0.303112  
26  0.000836  0.000514  0.000514   0.000701  7.467293  

[3 rows x 605 columns]


In [55]:
final_output = {}
for step_value in unique_steps:
    df_step = impulses[impulses['Step'] == step_value]
    output_dict = {
        "step": step_value,
        "pulses": []
    }
    for impulse_value in df_step['Impulse'].unique():
        df_impulse = df_step[df_step['Impulse'] == impulse_value]
        if impulse_value % 1 == 0:
            pulses_dict={"pulse": impulse_value,
                        "pulses": { #Объект с импульсами не нужен, не буедм его считывать. Это ускорит дело.
                            "impulse_reper": df_impulse[df_impulse['Channel']=='Reper'].iloc[:,3:603].values.flatten().tolist(),
                            "impulse_analyt": df_impulse[df_impulse['Channel']=='Analyt'].iloc[:,3:603].values.flatten().tolist(),
                        },
                        "threshold_analyt": list(df_impulse[df_impulse['Channel'] == 'Analyt']['Threshold'])[0],
                        "amplitude_reper": round(list(df_impulse[df_impulse['Channel'] == 'Reper']['Sum'])[0],8),
                        "amplitude_analyt": round(list(df_impulse[df_impulse['Channel'] == 'Analyt']['Sum'])[0],8)
                        }
            output_dict['pulses'].append(pulses_dict)
    final_output[str(f"step_{step_value}")] = output_dict #Вот из этого объекта легко получим все данные.

In [56]:
keys = list(final_output.keys())
for i in final_output[keys[0]]["pulses"]:
    print(i["amplitude_analyt"], i["pulses"])
#    print(i["threshold_analyt"], i["amplitude_analyt"])


4.6492567 {'impulse_reper': [0.002452340000000001, 0.0018073400000000015, 0.0014853400000000014, 0.0018073400000000015, 0.0018073400000000015, 0.0018073400000000015, 0.0021293400000000013, 0.0018073400000000015, 0.0021293400000000013, 0.0018073400000000015, 0.0018073400000000015, 0.0021293400000000013, 0.0018073400000000015, 0.0018073400000000015, 0.0014853400000000014, 0.0014853400000000014, 0.0018073400000000015, 0.0014853400000000014, 0.002452340000000001, 0.0021293400000000013, 0.0018073400000000015, 0.0021293400000000013, 0.0021293400000000013, 0.0014853400000000014, 0.002452340000000001, 0.0030963400000000017, 0.0014853400000000014, 0.002452340000000001, 0.002452340000000001, 1.15280734, 0.62646034, 0.68737934, 0.68189934, 0.68254434, 0.68641234, 0.68415634, 0.68093234, 0.65418034, 0.39342434, 0.18456234000000002, 0.04822134, 0.021468340000000002, 0.02017934, 0.01921234, 0.01792334, 0.01727834, 0.01663434, 0.01598934, 0.015344340000000001, 0.015344340000000001, 0.01437734, 0.0137